In [1]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import MinMaxScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

In [4]:
#데이터 경로의 경우 사용자의 환경에 맞게 설정해야 합니다.
df_train = pd.read_csv("C:/Users/User/Downloads/train.csv", encoding = "UTF-8")
df_test = pd.read_csv("C:/Users/User/Downloads/test (1).csv", encoding = "UTF-8")

In [7]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  891 non-null    int64  
 1   Survived     891 non-null    int64  
 2   Pclass       891 non-null    int64  
 3   Name         891 non-null    object 
 4   Sex          891 non-null    object 
 5   Age          714 non-null    float64
 6   SibSp        891 non-null    int64  
 7   Parch        891 non-null    int64  
 8   Ticket       891 non-null    object 
 9   Fare         891 non-null    float64
 10  Cabin        204 non-null    object 
 11  Embarked     889 non-null    object 
dtypes: float64(2), int64(5), object(5)
memory usage: 83.7+ KB


In [8]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 418 entries, 0 to 417
Data columns (total 11 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  418 non-null    int64  
 1   Pclass       418 non-null    int64  
 2   Name         418 non-null    object 
 3   Sex          418 non-null    object 
 4   Age          332 non-null    float64
 5   SibSp        418 non-null    int64  
 6   Parch        418 non-null    int64  
 7   Ticket       418 non-null    object 
 8   Fare         417 non-null    float64
 9   Cabin        91 non-null     object 
 10  Embarked     418 non-null    object 
dtypes: float64(2), int64(4), object(5)
memory usage: 36.0+ KB


In [9]:
df_train

PassengerId  Survived  Pclass  \
0              1         0       3   
1              2         1       1   
2              3         1       3   
3              4         1       1   
4              5         0       3   
..           ...       ...     ...   
886          887         0       2   
887          888         1       1   
888          889         0       3   
889          890         1       1   
890          891         0       3   

                                                  Name     Sex   Age  SibSp  \
0                              Braund, Mr. Owen Harris    male  22.0      1   
1    Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                               Heikkinen, Miss. Laina  female  26.0      0   
3         Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                             Allen, Mr. William Henry    male  35.0      0   
..                                                 ...     ...   ...    ...   
886                              Montvila, Rev. Juozas    male  27.0      0   
887                       Graham, Miss. Margaret Edith  female  19.0      0   
888           Johnston, Miss. Catherine Helen "Carrie"  female   NaN      1   
889                              Behr, Mr. Karl Howell    male  26.0      0   
890                                Dooley, Mr. Patrick    male  32.0      0   

     Parch            Ticket     Fare Cabin Embarked  
0        0         A/5 21171   7.2500   NaN        S  
1        0          PC 17599  71.2833   C85        C  
2        0  STON/O2. 3101282   7.9250   NaN        S  
3        0            113803  53.1000  C123        S  
4        0            373450   8.0500   NaN        S  
..     ...               ...      ...   ...      ...  
886      0            211536  13.0000   NaN        S  
887      0            112053  30.0000   B42        S  
888      2        W./C. 6607  23.4500   NaN        S  
889      0            111369  30.0000  C148        C  
890      0            370376   7.7500   NaN        Q  

[891 rows x 12 columns]

In [10]:
df_train.isnull().sum()

PassengerId      0
Survived         0
Pclass           0
Name             0
Sex              0
Age            177
SibSp            0
Parch            0
Ticket           0
Fare             0
Cabin          687
Embarked         2
dtype: int64

In [16]:
df_train['Age'] = df_train["Age"].fillna(df_train['Age'].mean())
df_train['Fare'] = df_train["Fare"].fillna(df_train['Fare'].mean())
df_train['Embarked'] = df_train["Embarked"].fillna(df_train["Embarked"].mode().iloc[0])
df_test['Age'] = df_test["Age"].fillna(df_test['Age'].mean())
df_test['Fare'] = df_test["Fare"].fillna(df_test['Fare'].mean())
df_test['Embarked'] = df_test["Embarked"].fillna(df_test["Embarked"].mode().iloc[0])

In [17]:
df_train

PassengerId  Survived  Pclass  \
0              1         0       3   
1              2         1       1   
2              3         1       3   
3              4         1       1   
4              5         0       3   
..           ...       ...     ...   
886          887         0       2   
887          888         1       1   
888          889         0       3   
889          890         1       1   
890          891         0       3   

                                                  Name     Sex        Age  \
0                              Braund, Mr. Owen Harris    male  22.000000   
1    Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.000000   
2                               Heikkinen, Miss. Laina  female  26.000000   
3         Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.000000   
4                             Allen, Mr. William Henry    male  35.000000   
..                                                 ...     ...        ...   
886                              Montvila, Rev. Juozas    male  27.000000   
887                       Graham, Miss. Margaret Edith  female  19.000000   
888           Johnston, Miss. Catherine Helen "Carrie"  female  29.699118   
889                              Behr, Mr. Karl Howell    male  26.000000   
890                                Dooley, Mr. Patrick    male  32.000000   

     SibSp  Parch            Ticket     Fare Cabin Embarked  
0        1      0         A/5 21171   7.2500   NaN        S  
1        1      0          PC 17599  71.2833   C85        C  
2        0      0  STON/O2. 3101282   7.9250   NaN        S  
3        1      0            113803  53.1000  C123        S  
4        0      0            373450   8.0500   NaN        S  
..     ...    ...               ...      ...   ...      ...  
886      0      0            211536  13.0000   NaN        S  
887      0      0            112053  30.0000   B42        S  
888      1      2        W./C. 6607  23.4500   NaN        S  
889      0      0            111369  30.0000  C148        C  
890      0      0            370376   7.7500   NaN        Q  

[891 rows x 12 columns]

In [18]:
df_train.isnull().sum()

PassengerId      0
Survived         0
Pclass           0
Name             0
Sex              0
Age              0
SibSp            0
Parch            0
Ticket           0
Fare             0
Cabin          687
Embarked         0
dtype: int64

In [19]:
df_test.isnull().sum()

PassengerId      0
Pclass           0
Name             0
Sex              0
Age              0
SibSp            0
Parch            0
Ticket           0
Fare             0
Cabin          327
Embarked         0
dtype: int64

In [20]:
df_train[['Age', 'Fare']] = df_train[['Age', 'Fare']].applymap(lambda x: np.round(x) if pd.notnull(x) else x)
df_test[['Age', 'Fare']] = df_test[['Age', 'Fare']].applymap(lambda x: np.round(x) if pd.notnull(x) else x)


In [24]:
df_train['Sex'] = df_train['Sex'].map({'male':0, 'female':1})
df_train['Embarked'] = df_train['Embarked'].map({'S':0, 'C':1, 'Q':2})
df_test['Sex'] = df_test['Sex'].map({'male':0, 'female':1})
df_test['Embarked'] = df_test['Embarked'].map({'S':0, 'C':1, 'Q':2})

In [25]:
df_train

PassengerId  Survived  Pclass  \
0              1         0       3   
1              2         1       1   
2              3         1       3   
3              4         1       1   
4              5         0       3   
..           ...       ...     ...   
886          887         0       2   
887          888         1       1   
888          889         0       3   
889          890         1       1   
890          891         0       3   

                                                  Name  Sex   Age  SibSp  \
0                              Braund, Mr. Owen Harris    0  22.0      1   
1    Cumings, Mrs. John Bradley (Florence Briggs Th...    1  38.0      1   
2                               Heikkinen, Miss. Laina    1  26.0      0   
3         Futrelle, Mrs. Jacques Heath (Lily May Peel)    1  35.0      1   
4                             Allen, Mr. William Henry    0  35.0      0   
..                                                 ...  ...   ...    ...   
886                              Montvila, Rev. Juozas    0  27.0      0   
887                       Graham, Miss. Margaret Edith    1  19.0      0   
888           Johnston, Miss. Catherine Helen "Carrie"    1  30.0      1   
889                              Behr, Mr. Karl Howell    0  26.0      0   
890                                Dooley, Mr. Patrick    0  32.0      0   

     Parch            Ticket  Fare Cabin  Embarked  
0        0         A/5 21171   7.0   NaN         0  
1        0          PC 17599  71.0   C85         1  
2        0  STON/O2. 3101282   8.0   NaN         0  
3        0            113803  53.0  C123         0  
4        0            373450   8.0   NaN         0  
..     ...               ...   ...   ...       ...  
886      0            211536  13.0   NaN         0  
887      0            112053  30.0   B42         0  
888      2        W./C. 6607  23.0   NaN         0  
889      0            111369  30.0  C148         1  
890      0            370376   8.0   NaN         2  

[891 rows x 12 columns]

In [26]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 891 entries, 0 to 890
Data columns (total 12 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   PassengerId  891 non-null    int64  
 1   Survived     891 non-null    int64  
 2   Pclass       891 non-null    int64  
 3   Name         891 non-null    object 
 4   Sex          891 non-null    int64  
 5   Age          891 non-null    float64
 6   SibSp        891 non-null    int64  
 7   Parch        891 non-null    int64  
 8   Ticket       891 non-null    object 
 9   Fare         891 non-null    float64
 10  Cabin        204 non-null    object 
 11  Embarked     891 non-null    int64  
dtypes: float64(2), int64(7), object(3)
memory usage: 83.7+ KB


In [30]:
#Train data의 One-hot Encoding
tr_pclass_dummies = pd.get_dummies(df_train['Pclass'], prefix='Pclass')
tr_embarked_dummies = pd.get_dummies(df_train['Embarked'], prefix='Embarked')
df_train = pd.concat([df_train, tr_pclass_dummies, tr_embarked_dummies], axis=1)
df_train = df_train.drop(['Pclass', 'Embarked'], axis=1)

#Test data의 One-hot Encoding
te_pclass_dummies = pd.get_dummies(df_test['Pclass'], prefix='Pclass')
te_embarked_dummies = pd.get_dummies(df_test['Embarked'], prefix='Embarked')
df_test = pd.concat([df_test, te_pclass_dummies, te_embarked_dummies], axis=1)
df_test = df_test.drop(['Pclass', 'Embarked'], axis=1)

In [31]:
df_train

PassengerId  Survived                                               Name  \
0              1         0                            Braund, Mr. Owen Harris   
1              2         1  Cumings, Mrs. John Bradley (Florence Briggs Th...   
2              3         1                             Heikkinen, Miss. Laina   
3              4         1       Futrelle, Mrs. Jacques Heath (Lily May Peel)   
4              5         0                           Allen, Mr. William Henry   
..           ...       ...                                                ...   
886          887         0                              Montvila, Rev. Juozas   
887          888         1                       Graham, Miss. Margaret Edith   
888          889         0           Johnston, Miss. Catherine Helen "Carrie"   
889          890         1                              Behr, Mr. Karl Howell   
890          891         0                                Dooley, Mr. Patrick   

     Sex   Age  SibSp  Parch            Ticket  Fare Cabin  Pclass_1  \
0      0  22.0      1      0         A/5 21171   7.0   NaN         0   
1      1  38.0      1      0          PC 17599  71.0   C85         1   
2      1  26.0      0      0  STON/O2. 3101282   8.0   NaN         0   
3      1  35.0      1      0            113803  53.0  C123         1   
4      0  35.0      0      0            373450   8.0   NaN         0   
..   ...   ...    ...    ...               ...   ...   ...       ...   
886    0  27.0      0      0            211536  13.0   NaN         0   
887    1  19.0      0      0            112053  30.0   B42         1   
888    1  30.0      1      2        W./C. 6607  23.0   NaN         0   
889    0  26.0      0      0            111369  30.0  C148         1   
890    0  32.0      0      0            370376   8.0   NaN         0   

     Pclass_2  Pclass_3  Embarked_0  Embarked_1  Embarked_2  
0           0         1           1           0           0  
1           0         0           0           1           0  
2           0         1           1           0           0  
3           0         0           1           0           0  
4           0         1           1           0           0  
..        ...       ...         ...         ...         ...  
886         1         0           1           0           0  
887         0         0           1           0           0  
888         0         1           1           0           0  
889         0         0           0           1           0  
890         0         1           0           0           1  

[891 rows x 16 columns]

In [145]:
high_sibsp_threshold = 3
#3를 기준으로 3보다 작을 경우 1, 3이상일 경우 0의 값을 가지는 새로운 Column 생성
df_train['High_SibSp'] = (df_train['SibSp'] < high_sibsp_threshold).astype(int)
df_test['High_SibSp'] = (df_test['SibSp'] < high_sibsp_threshold).astype(int)


In [146]:
# Specify the three columns of interest
columns_of_interest = ['High_SibSp', 'Survived']

# Calculate the correlation coefficient for the specified columns
correlation_matrix = df_train[columns_of_interest].corr()

# Display the correlation matrix
print(correlation_matrix)

            High_SibSp  Survived
High_SibSp    1.000000  0.111145
Survived      0.111145  1.000000


In [147]:
df_train

PassengerId  Survived                                               Name  \
0              1         0                            Braund, Mr. Owen Harris   
1              2         1  Cumings, Mrs. John Bradley (Florence Briggs Th...   
2              3         1                             Heikkinen, Miss. Laina   
3              4         1       Futrelle, Mrs. Jacques Heath (Lily May Peel)   
4              5         0                           Allen, Mr. William Henry   
..           ...       ...                                                ...   
886          887         0                              Montvila, Rev. Juozas   
887          888         1                       Graham, Miss. Margaret Edith   
888          889         0           Johnston, Miss. Catherine Helen "Carrie"   
889          890         1                              Behr, Mr. Karl Howell   
890          891         0                                Dooley, Mr. Patrick   

     Sex   Age  SibSp  Parch            Ticket  Fare Cabin  Pclass_1  \
0      0  22.0      1      0         A/5 21171   7.0   NaN         0   
1      1  38.0      1      0          PC 17599  71.0   C85         1   
2      1  26.0      0      0  STON/O2. 3101282   8.0   NaN         0   
3      1  35.0      1      0            113803  53.0  C123         1   
4      0  35.0      0      0            373450   8.0   NaN         0   
..   ...   ...    ...    ...               ...   ...   ...       ...   
886    0  27.0      0      0            211536  13.0   NaN         0   
887    1  19.0      0      0            112053  30.0   B42         1   
888    1  30.0      1      2        W./C. 6607  23.0   NaN         0   
889    0  26.0      0      0            111369  30.0  C148         1   
890    0  32.0      0      0            370376   8.0   NaN         0   

     Pclass_2  Pclass_3  Embarked_0  Embarked_1  Embarked_2  High_SibSp  
0           0         1           1           0           0           1  
1           0         0           0           1           0           1  
2           0         1           1           0           0           1  
3           0         0           1           0           0           1  
4           0         1           1           0           0           1  
..        ...       ...         ...         ...         ...         ...  
886         1         0           1           0           0           1  
887         0         0           1           0           0           1  
888         0         1           1           0           0           1  
889         0         0           0           1           0           1  
890         0         1           0           0           1           1  

[891 rows x 17 columns]

In [151]:
df_test

PassengerId                                          Name  Sex   Age  \
0            892                              Kelly, Mr. James    0  34.0   
1            893              Wilkes, Mrs. James (Ellen Needs)    1  47.0   
2            894                     Myles, Mr. Thomas Francis    0  62.0   
3            895                              Wirz, Mr. Albert    0  27.0   
4            896  Hirvonen, Mrs. Alexander (Helga E Lindqvist)    1  22.0   
..           ...                                           ...  ...   ...   
413         1305                            Spector, Mr. Woolf    0  30.0   
414         1306                  Oliva y Ocana, Dona. Fermina    1  39.0   
415         1307                  Saether, Mr. Simon Sivertsen    0  38.0   
416         1308                           Ware, Mr. Frederick    0  30.0   
417         1309                      Peter, Master. Michael J    0  30.0   

     SibSp  Parch              Ticket   Fare Cabin  Pclass_1  Pclass_2  \
0        0      0              330911    8.0   NaN         0         0   
1        1      0              363272    7.0   NaN         0         0   
2        0      0              240276   10.0   NaN         0         1   
3        0      0              315154    9.0   NaN         0         0   
4        1      1             3101298   12.0   NaN         0         0   
..     ...    ...                 ...    ...   ...       ...       ...   
413      0      0           A.5. 3236    8.0   NaN         0         0   
414      0      0            PC 17758  109.0  C105         1         0   
415      0      0  SOTON/O.Q. 3101262    7.0   NaN         0         0   
416      0      0              359309    8.0   NaN         0         0   
417      1      1                2668   22.0   NaN         0         0   

     Pclass_3  Embarked_0  Embarked_1  Embarked_2  High_SibSp  
0           1           0           0           1           1  
1           1           1           0           0           1  
2           0           0           0           1           1  
3           1           1           0           0           1  
4           1           1           0           0           1  
..        ...         ...         ...         ...         ...  
413         1           1           0           0           1  
414         0           0           1           0           1  
415         1           1           0           0           1  
416         1           1           0           0           1  
417         1           0           1           0           1  

[418 rows x 16 columns]

In [155]:
x_train = df_train.drop(['PassengerId','Survived', 'Name', 'SibSp', 'Cabin', 'Ticket'], axis = 1)
y_train = df_train['Survived']


In [156]:
x_train

Sex   Age  Parch  Fare  Pclass_1  Pclass_2  Pclass_3  Embarked_0  \
0      0  22.0      0   7.0         0         0         1           1   
1      1  38.0      0  71.0         1         0         0           0   
2      1  26.0      0   8.0         0         0         1           1   
3      1  35.0      0  53.0         1         0         0           1   
4      0  35.0      0   8.0         0         0         1           1   
..   ...   ...    ...   ...       ...       ...       ...         ...   
886    0  27.0      0  13.0         0         1         0           1   
887    1  19.0      0  30.0         1         0         0           1   
888    1  30.0      2  23.0         0         0         1           1   
889    0  26.0      0  30.0         1         0         0           0   
890    0  32.0      0   8.0         0         0         1           0   

     Embarked_1  Embarked_2  High_SibSp  
0             0           0           1  
1             1           0           1  
2             0           0           1  
3             0           0           1  
4             0           0           1  
..          ...         ...         ...  
886           0           0           1  
887           0           0           1  
888           0           0           1  
889           1           0           1  
890           0           1           1  

[891 rows x 11 columns]

In [157]:
y_train

0      0
1      1
2      1
3      1
4      0
      ..
886    0
887    1
888    0
889    1
890    0
Name: Survived, Length: 891, dtype: int64

In [158]:
svm_model = SVC()

svm_model.fit(x_train, y_train)

SVC()

In [160]:
x_test = df_test.drop(['PassengerId', 'Name', 'SibSp', 'Cabin', 'Ticket'], axis = 1)

In [162]:
x_train

Sex   Age  Parch  Fare  Pclass_1  Pclass_2  Pclass_3  Embarked_0  \
0      0  22.0      0   7.0         0         0         1           1   
1      1  38.0      0  71.0         1         0         0           0   
2      1  26.0      0   8.0         0         0         1           1   
3      1  35.0      0  53.0         1         0         0           1   
4      0  35.0      0   8.0         0         0         1           1   
..   ...   ...    ...   ...       ...       ...       ...         ...   
886    0  27.0      0  13.0         0         1         0           1   
887    1  19.0      0  30.0         1         0         0           1   
888    1  30.0      2  23.0         0         0         1           1   
889    0  26.0      0  30.0         1         0         0           0   
890    0  32.0      0   8.0         0         0         1           0   

     Embarked_1  Embarked_2  High_SibSp  
0             0           0           1  
1             1           0           1  
2             0           0           1  
3             0           0           1  
4             0           0           1  
..          ...         ...         ...  
886           0           0           1  
887           0           0           1  
888           0           0           1  
889           1           0           1  
890           0           1           1  

[891 rows x 11 columns]

In [163]:
x_test

Sex   Age  Parch   Fare  Pclass_1  Pclass_2  Pclass_3  Embarked_0  \
0      0  34.0      0    8.0         0         0         1           0   
1      1  47.0      0    7.0         0         0         1           1   
2      0  62.0      0   10.0         0         1         0           0   
3      0  27.0      0    9.0         0         0         1           1   
4      1  22.0      1   12.0         0         0         1           1   
..   ...   ...    ...    ...       ...       ...       ...         ...   
413    0  30.0      0    8.0         0         0         1           1   
414    1  39.0      0  109.0         1         0         0           0   
415    0  38.0      0    7.0         0         0         1           1   
416    0  30.0      0    8.0         0         0         1           1   
417    0  30.0      1   22.0         0         0         1           0   

     Embarked_1  Embarked_2  High_SibSp  
0             0           1           1  
1             0           0           1  
2             0           1           1  
3             0           0           1  
4             0           0           1  
..          ...         ...         ...  
413           0           0           1  
414           1           0           1  
415           0           0           1  
416           0           0           1  
417           1           0           1  

[418 rows x 11 columns]

In [164]:
y_pred = svm_model.predict(x_test)

In [165]:
y_pred

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0,
       0, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0,
       0, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0,
       0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0,
       0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0,
       0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 1, 0, 0,
       1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0,

In [173]:
from pandas import DataFrame
predictions_df = pd.DataFrame(y_pred, columns=['Survived'])

predictions_df['PassengerId'] = df_test['PassengerId']

predictions_df = predictions_df[['PassengerId', 'Survived']]

predictions_df.to_csv("predicted_survived_with_passengerid.csv", index=False)